In [13]:
import requests
import urllib
import json
import time
import csv
import pandas as pd
import math
import queue
import threading
from multiprocessing.dummy import Pool as ThreadPool

correct_mapping = {
    "ship": "vận chuyển",
    "shop": "cửa hàng",
    " m ": " mình ",
    " mik ": " mình ",
    " k ": " không ",
    " kh ": " không ",
    " tl ": " trả lời ",
    " r ": " rồi ",
    " fb ": " mạng xã hội ", # facebook
    " face ": " mạng xã hội ",
    " thanks ": " cảm ơn ",
    "thank": "cảm ơn",
    " tks ": " cảm ơn ", 
    " tk ": " cảm ơn ",
    " toẹt vời ": " tuyệt vời ",
    " bit ": " biết "
}

def call_segment(sentence):
    correct_sentence = sentence
    sentence_encode = urllib.parse.quote_plus(sentence)
    url_str = 'http://10.30.152.12:6565/segment?query=' + sentence_encode
    try:
        response = requests.get(url_str, timeout=50)
        correct_sentence = response.text.rstrip()
        
        json_string = json.loads(response.text)
        output = ''
        for word in json_string:
            output += word['text'].replace(' ', '_') + ' '
    except requests.Timeout:
        print('timeout')
        return sentence
    return output

# print(call_segment("chương trình của đài truyền hình hà nội "))

def call_service(sentence):
    correct_sentence = sentence
    sentence_encode = urllib.parse.quote_plus(sentence)
#     url_str = 'http://10.30.152.13:9195/checking?checkingSentence=' + sentence_encode
    
    try:
#         response = requests.get(url_str, timeout=50)
        data = {"checkingSentence": sentence,
                "entities": [
                    {
                      "word": "mimax",
                      "start_index": 0,
                      "end_index": 7,
                      "synonym": "mimax70"
                    }
                  ],
                 "type": [
                    "telex",
                    "duplicate",
                    "abbr",
                    "dict",
                    "teencode",
                    "addTone"
                  ]
               }
        response = requests.post("http://10.30.152.13:9195/spelling-detection/checking", data=json.dumps(data))
        json_string = json.loads(response.text)
#         print('json_string: ', json_string)
        for key in json_string:
            if "correctSentence" in key:
                correct_sentence = key['correctSentence']
        
#         correct_sentence = response.text.rstrip()
    except requests.Timeout:
        print('error 1')
        return sentence

    return correct_sentence


def doTask(sentences, count, start_time, thread_name):
    correct_sentence_list = []
    count_sentence = 0
    for sentence in sentences:
        count_sentence += 1
        correct_sentence = call_service(sentence)
        correct_sentence = call_segment(correct_sentence)
        correct_sentence_list.append(correct_sentence)
        print('wrong sentence: ', sentence)
        print('correct sentence: ', correct_sentence)
        print('Total time so far: ', time.time() - start_time, 's')
        print(thread_name, ' - sentence ', count_sentence, '/', len(sentences), ' of cluster ', count)
    print('writing file')
    with open('output'+threadname+'.txt') as fw:
        for sentence in correct_sentence_list:
            print('writing')
            fw.write(sentence)
    print('***************FINISH*****************: ', thread_name)
    return correct_sentence_list


def calculateParallel(sentence_partition, threads, count, start_time):
    input = []
    count_thread = 0
    for wrong_sentence_list in sentence_partition:
        count_thread += 1
        thread_name = 'thread' + str(count_thread)
        input.append((wrong_sentence_list, count, start_time, thread_name))
        
    pool = ThreadPool(threads)
    results = pool.starmap(doTask, input)
    pool.close()
    pool.join()
    return results

def get_correct_sentence_multithread(sentences, count, start_time):
    num_thread = 10
    print('sentence size: ', len(sentences))
    sentence_partition = []
    partition_size = math.floor(len(sentences) / num_thread)
    start = 0
    for i in range(num_thread - 1):
        end = partition_size * (i + 1)
        print('start: ', start, ' - end: ', end)
        sentence_partition.append(sentences[start:end])
        start = end
    print('start: ', start)
    sentence_partition.append(sentences[start:])
    correct_sentence_list = calculateParallel(sentence_partition, num_thread, count, start_time)
    for i in range(len(correct_sentence_list)):
        print('xxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxx')
    print('**************** FINISH PARALLEL *******************')
    return correct_sentence_list
    

# def get_correct_sentence(input, output):
#     start_time = time.time()
#     with open(input, 'r') as f:
#         sentences = []
#         count = 0
#         for line in f:
#             sentences.append(line)
#             if len(sentences) == 10000:
#                 count += len(sentences)
#                 print('..........START MULTITHREAD..........')
#                 correct_sentence = get_correct_sentence_multithread(sentences, count, start_time)
#                 print('..........WRITE FILE...........')
#                 write_list(correct_sentence, output)
#                 print('..........FINISH WRITING FILE...........')
#                 del sentences[:]

#             count += len(sentences)
#             correct_sentence = get_correct_sentence_multithread(sentences, count, start_time)
#             write_list(correct_sentence, output)
#             return correct_sentence
   
    
def get_correct_sentence(comment, output):
    start_time = time.time()
    print('comment: ', comment)
    correct_sentence = get_correct_sentence_multithread(comment, 1, start_time)
    write_list(correct_sentence, output)
    return correct_sentence
        

def write_list(sentences, file):
    with open(file, 'a') as f:
        for sentence in sentences:
            for sen in sentence:
                print('writing sentence: ', sen)
                f.write(sen + '\n')
    f.close()
        
#get_correct_sentence('data/manual_pairs.txt', 'data/manual_predicted.csv')

def load_raw_data(filename, is_train=True):

    sample = []
    sample_list = []

    regex = 'train_'
    if not is_train:
        regex = 'test_'
    
    with open(filename, 'r') as file:
        for line in file :
            if regex in line:
                sample_list.append(sample)
                sample = [line]
            elif line!='\n':
                sample.append(line)

    sample_list.append(sample)      

    return sample_list[1:]

def save_csv(csv_file, input_file, is_train=True):
    sample_list = load_raw_data(input_file, is_train)
    print('len sample list: ', len(sample_list))
            
    with open(csv_file, 'w') as fo:
        writer = csv.writer(fo)
        count = 0
        id, label, comment = [], [], []
        if is_train:
            writer.writerow(['id','comment','label'])
            for sample in sample_list:
                count += 1
                print('\r count = %i' % count, end = '\r')
                id.append(sample[0].replace('\n',''))
                label.append(sample[-1])
                comment.append(' SPLIT '.join(sample[1:-1]).replace('\n',''))
            correct_comment = get_correct_sentence(comment, 'train_output_cmt.txt')
#             with open('train_output_cmt.txt', 'r') as fr:
#                 correct_comment = [line for line in fr]
            for i in range(len(correct_comment)):
                writer.writerow([id[i], correct_comment[i], label[i]])
                
        elif not is_train:
            writer.writerow(['id', 'comment'])
            for sample in sample_list:
                count += 1
                print('\r count = %i' % count, end = '\r')
                id.append(sample[0].replace('\n',''))
                comment.append(' SPLIT '.join(sample[1:]).replace('\n',''))
            correct_comment = get_correct_sentence(comment, 'test_output_cmt.txt')
#             with open('test_output_cmt.txt', 'r') as fr:
#                 correct_comment = [line for line in fr]
            for i in range(len(correct_comment)):
                writer.writerow([id[i], correct_comment[i]])

save_csv('test_correct_segment.csv', 'test.crash', is_train=False)
# save_csv('train_correct_segment.csv', 'train.crash', is_train=True)

# print(call_service('ac muốn gì'))

# train_df = pd.read_csv("train.csv")
# train_df.info()  
# train_df.head(5)
# comment = train_df["comment"]
# print(comment)

len sample list:  10981


 count = 5920

comment:  ['"Chưa dùng thử nên chưa biết"', '" Không đáng tiềnVì ngay đợt sale nên mới mua nhưng sp thì như đã qua sử dụng ! Đã nt trao đổi vs shop cũng đưa ra cách giải quyết nhưng kg được đổi hàng mà chỉ hoàn tiền !! Nên mình quyết định kg đổi hàng vì kg có time  chỉ muốn đánh giá sp như những gì mình nhận được !"', '"Cám ơn shop. Đóng gói sản phẩm rất đẹp và chắc chắn"', '"Vải đẹp.phom oki luôn.quá ưng"', '"Chuẩn hàng đóng gói đẹp"', '" Đóng gói sản phẩm rất đẹp và chắc chắn Shop phục vụ rất tốt it so good"', '"Sau khi đọc xong cuốn truyện thì cảm xúc của mình cũng vụt trôi đi mất.Truyện theo mô típ cũ quen thuộc.Miêu tả chưa đặc sắcmột vài tình tiết nhàm chánvô lí.Mình vốn thích chị Kawi nhưng lần này mình lại thất vọngthực sự ko đáng bỏ tiền ra mua.Nhân vật nam theo kiểu đẹp trainhà giàubad boy...thưng sự là rất chán.Mình shock khi đọc nó thật.Nữ chính thì quá tầm thườngkiểu ngoài mạnh trong mềm như bánh bèolúc đầu

wrong sentence:  "Đầu tiên là kiểu dáng: nhìn trên hình rất đẹp rất sang nhưng thực tế thì màu của cây Mascara này hơi xỉn và tối nhìn không sang chút nào.Về chất lượng không biết là do cây của mình bị lỗi hay sao chứ mình thấy chất mascara này cứ khô khô làm sao ấy mình dùng khá nhiều loại rồi cả mascara của Maybeline cũng từng dùng nhưng đến cây này hơi thất vọng dùng mà cứ như mấy cây mascara cũ của mình dùng gần hết rồi ấy apply lên mi cũng ko thấy hiệu quả lắm."
correct sentence:  " Đầu_tiên là kiểu_dáng : nhìn trên hình rất đẹp rất sang nhưng thực_tế thì màu của cây Mascara này hơi xỉn và tối nhìn không sang chút nào.Về chất_lượng không biết là do cây của mình bị lỗi hay sao chứ mình thấy chất mascara này cứ khô khô làm_sao ấy mình dùng khá nhiều loại rồi cả mascara của Maybeline cũng từng dùng nhưng đến cây này hơi thất_vọng dùng mà cứ như mấy cây mascara cũ của mình dùng gần hết rồi ấy apply lên mi cũng ko thấy hiệu_quả lắm . " 
Total time so far:  0.17485857009887695 s
thread6

wrong sentence:  "Cám ơn shop. Đóng gói sản phẩm rất đẹp và chắc chắn"
correct sentence:  cám_ơn shop đóng_gói sản_phẩm rất đẹp và chắc_chắn 
Total time so far:  3.2073230743408203 s
thread1  - sentence  3 / 1098  of cluster  1
wrong sentence:  "Giao hàng thiếu công tắc gọi điện báo rồi vẫn không thấy"
correct sentence:  giao hàng thiếu công_tắc gọi điện báo rồi vẫn không thấy 
Total time so far:  3.341623067855835 s
thread5  - sentence  2 / 1098  of cluster  1
wrong sentence:  "Vải đẹp.phom oki luôn.quá ưng"
correct sentence:  vải đẹpphom oki luônquá ưng 
Total time so far:  3.4149911403656006 s
thread1  - sentence  4 / 1098  of cluster  1
wrong sentence:  "chất lượng tệ hàng ko như hình SPLIT đỗ long tùn lum"
correct sentence:  chất_lượng tệ hàng không như hình split đỗ long tùn lum 
Total time so far:  3.6159074306488037 s
thread8  - sentence  2 / 1098  of cluster  1
wrong sentence:  "Chuẩn hàng đóng gói đẹp"
correct sentence:  chuẩn hàng đóng_gói đẹp 
Total time so far:  3.70206570

...

wrong sentence:  "Bình thường mua thẻ cào khoảng 5 đến 10 phút là nhận được mã lần này chờ đến ngày thứ 3 chậm quá shop ah lần sau chuyển nhanh hơn nhé."
correct sentence:  bình_thường mua thẻ cào khoảng 5 đến 10 phút là nhận được mã lần này chờ đến ngày thứ 3 chậm quá shop ah lần sau chuyển nhanh hơn nhé 
Total time so far:  1425.4832484722137 s
thread10  - sentence  1051 / 1099  of cluster  1
wrong sentence:  "Sách mình nhận đc như sách used vậy bẩn ngoài bìa đã đành ở trong cũng có vết bẩn"
correct sentence:  sách mình nhận được như sách used vậy bẩn ngoài bìa đã_đành ở trong cũng có vết bẩn 
Total time so far:  1425.525137424469 s
thread3  - sentence  1087 / 1098  of cluster  1
wrong sentence:  "Chất lương sp tốt "
correct sentence:  chất_lượng sp tốt 
Total time so far:  1425.667338848114 s
thread3  - sentence  1088 / 1098  of cluster  1
wrong sentence:  " Chất lượng sản phẩm tuyệt vời Đóng gói sản phẩm rất đẹp và chắc chắn Chất lượng sản phẩm tuyệt vời Đóng gói sản phẩm rất đẹp v

wrong sentence:  "Balo hoi nho so voi hinh  Đóng gói sản phẩm rất đẹp và chắc chắn"
correct sentence:  balo hơi nhỏ so với hình đóng_gói sản_phẩm rất đẹp và chắc_chắn 
Total time so far:  1430.045881986618 s
thread2  - sentence  1090 / 1098  of cluster  1
wrong sentence:  "Thái độ chăm sóc khách hàng kém dù khách hàng đã mua nhiều đơn. Không lắng nghe góp ý chân thành từ khách hàng để nâng cao chất lượng hàng bán mà đổ lỗi cho bên giao hàng và lỗi tỷ lệ hạt hư là do cuối vụ cách nói như muốn cãi nhau với khách hàng. Không thể chấp nhận được! "
correct sentence:  thái_độ chăm_sóc khách_hàng kém dù khách_hàng đã mua nhiều đơn không lắng_nghe góp_ý chân_thành từ khách_hàng để nâng cao chất_lượng hàng bán mà đổ lỗi cho bên giao hàng và lỗi tỷ_lệ hạt hư là do cuối vụ cách nói như muốn cãi nhau với khách_hàng không_thể chấp_nhận được 
Total time so far:  1430.7134833335876 s
thread10  - sentence  1056 / 1099  of cluster  1
wrong sentence:  "Xai ok"
correct sentence:  xài ok 
Total time so fa

wrong sentence:  "Mua 2 đôi và đã bị rách mất 1 đôi . dép k đẹp vải bị ra màu phần quay nhỏ hơn so với trên ảnh"
correct sentence:  mua 2 đôi và đã bị rách mất 1 đôi dép không đẹp vải bị ra màu phần quay nhỏ hơn so với trên ảnh 
Total time so far:  1435.3640825748444 s
thread3  - sentence  1097 / 1098  of cluster  1
wrong sentence:  "Gói sản phẩm thôsản phẩm kém mùi hươngkhông giữ được lâu quá 15'.Giao hàng nhanh."
correct sentence:  gói sản_phẩm thôsản phẩm kém mùi hươngkhông giữ được lâu quá 15 giao hàng nhanh 
Total time so far:  1435.4505145549774 s
thread5  - sentence  1077 / 1098  of cluster  1
wrong sentence:  " Chất lượng sản phẩm tuyệt vời. Không biết đi ăn mùng 1 âm thì có được không nhỉ😁😁😁"
correct sentence:  chất_lượng sản_phẩm tuyệt_vời không biết đi ăn mùng 1 âm thì có được không nhỉ 
Total time so far:  1435.6176533699036 s
thread2  - sentence  1098 / 1098  of cluster  1
writing file
wrong sentence:  "K tuyệt vì quá tuyệt ❤️"
correct sentence:  không tuyệt vì quá tuyệt 


wrong sentence:  "Giao sai mẫu  đặt màu này lại giao màu khác . Mới lần đầu mua hàng mà đã mất niềm tin rồi . Mong shop làm ăn uy tín hơn . "
correct sentence:  giao sai mẫu đặt màu này lại giao màu khác mới lần đầu mua hàng mà đã mất niềm tin rồi mong shop làm_ăn uy_tín hơn 
Total time so far:  1445.9712204933167 s
thread5  - sentence  1089 / 1098  of cluster  1
wrong sentence:  "Sản phẩm tốt nhưng hơi nhăn khi hàng về  Đóng gói sản phẩm rất đẹp và chắc chắn"
correct sentence:  sản_phẩm tốt nhưng hơi nhăn khi hàng về đóng_gói sản_phẩm rất đẹp và chắc_chắn 
Total time so far:  1446.514442205429 s
thread5  - sentence  1090 / 1098  of cluster  1
wrong sentence:  "Sản phẩm bị móp khi vận chuyển nhắn tin shop ko trả lời. Tuy nhiên thì sản phẩm dùng khá ok"
correct sentence:  sản_phẩm bị móp khi vận_chuyển nhắn_tin shop không trả_lời tuy_nhiên thì sản_phẩm dùng khá ok 
Total time so far:  1446.5824375152588 s
thread10  - sentence  1077 / 1099  of cluster  1
wrong sentence:  " Rất đáng tiền 

wrong sentence:  " Thời gian giao hàng rất nhanh.ngon.mà cay quá... Chất lượng sản phẩm tuyệt vời"
correct sentence:  thời_gian giao hàng rất nhanhngonmà cây quá chất_lượng sản_phẩm tuyệt_vời 
Total time so far:  1455.6462235450745 s
thread10  - sentence  1095 / 1099  of cluster  1
wrong sentence:  "Sản phẩm hơi cũ"
correct sentence:  sản_phẩm hơi cũ 
Total time so far:  1455.7188057899475 s
thread10  - sentence  1096 / 1099  of cluster  1
wrong sentence:  "Sản phẩm chắc chắn nhưng k bóng bằng trong hình"
correct sentence:  sản_phẩm chắc_chắn nhưng không bóng bằng trong hình 
Total time so far:  1456.2024085521698 s
thread10  - sentence  1097 / 1099  of cluster  1
wrong sentence:  " Chất lượng sản phẩm tuyệt vời có mùi thơm rất dễ chịu"
correct sentence:  chất_lượng sản_phẩm tuyệt_vời có mùi thơm rất dễ_chịu 
Total time so far:  1456.3796081542969 s
thread10  - sentence  1098 / 1099  of cluster  1
wrong sentence:  "như quảng cáo. sim rất tốt"
correct sentence:  như quảng_cáo sim rất tố